In [1]:
#### specify path of Julia Code for 2D Models ####
### By default the working directory ./2D_Models ###
path = string( pwd(), "/2D_Models/")

"/home/jakob/Dokumente/Repositories/Modeling_Framework/2D_Models/"

In [27]:
##### include 2D Modelling Framework ####
include(string(path, "./2D_model_library.jl"));


########## OPERATIONAL ##########
##### how to chose the actual velocity? #####

#op_model = "Constant"
#op_model = "Collision_Free_Speed"
#op_model = "RVO"
#op_model = "SocialForce"
#op_model = "AV_Model"
#op_model = "AV_IN_Model"
op_model = "IN_Costfunction"
#op_model = "IN_Model"

#op_model = "Intrusion_Force"

include_op_model(op_model, path)

########## TACTICAL ##########
#### how to chose the preferred velocity? ###

tact_model = "Constant"
#tact_model = "IN_Model"

include_tact_model(tact_model, path)


########## STRATEGIC ##########
### how to chose the desired velocity ###

strat_model = "Constant"
#strat_model = "Towards_Goal"

include_strat_model(strat_model, path)


########## OPTIMIZATION SCHEME ##########
### If optimization of a cost-function is included, how to solve? ###

#optimization_scheme = "Regular_Sampling"
optimization_scheme = "Random_Sampling"

include_optimization_scheme(optimization_scheme, path)


##### which update scheme? #####

update = "Parallel_Update"
#update = "Step_Update"

include_update(update, path)


##### which order? i.e. Acceleration or Velocity based? ####
#order = "first"
order = "second"

include_order(order, path)


##### PERCEPTIONAL MODEL ####
perception_model = "None"
#perception_model = "Only_in_Front"

include_perception_model(perception_model, path)

In [28]:
#### parameters of the agents ####
p = [2.0, 1.5, 2.0, 1.0, 0.3, 0.0, 0.0, 0.1, 1.0, 1.0, 0.0, 0.0, 0.5, 0.0]
# ModelParameter: v_max, v_des, T, T2, l, step_time, τ_A, τ_R, α, β, ζ_h, ζ_v, r, ϕ
p_desc = "v_max, v_des, T, T2, l, step_time, τ_A, τ_R, α, β, ζ_h, ζ_v, r, ϕ"

### of the system ###
N = 180
system_size = (9.0, 5.0) #important for periodic boundaries

### of the simulation ###
sim_p = [0.0, 10.0, 0.05, 0.01, 3.0] #t_relax, t_max, dt_save, dt, r
sim_p_desc = "t_relax, t_max, dt_save, dt, r"

### initialize geometry ###
#geometrie = create_corridor(system_size[2], system_size[1], 0.1)
geometrie = create_geometry_single_obstacle((37.5,31.5), 0.0)

### initialize crowd ###
menge = create_crowd(N, geometrie)

Init_Hom_Vels!(menge, 1.0)
Init_Hom_Parameters!(p, menge)
Two_Approaching_Crowds(menge, geometrie, 9.0, Int(round(N)), system_size)

In [29]:
positions, headings = Simulate!(menge, geometrie, sim_p[1], sim_p[2], sim_p[3], sim_p[4], sim_p[5], system_size);

In [30]:
using GR
GR.inline("mov")

j = 1

dt_save = sim_p[3]
geometry_x, geometry_y = rewrite_geometry(geometrie)
boundaries_x, boundaries_y = boundaries_rectangle_positions(system_size)

while j*sim_p[3] < sim_p[2]-sim_p[1]
    
        GR.clearws()

        GR.setwindow(-1, 11, -1, 11)
        GR.setviewport(0.0, 1, 0.0, 1)
    
        plot_geometry(geometry_x, geometry_y, 0.8, 20)
        plot_boundaries(boundaries_x, boundaries_y, 0.2, 999)        
        
        plot_agents(positions[j, :], headings[j, :], 2.3, 100, 0.7, 999, 0.1)
    
        model = "AV*IN-model"
        timer = string("time ", round(j*dt_save, digits = 1), "s")
        GR.text(0.8, 0.95, timer)
        GR.text(0.8, 0.9, model)
        
        GR.updatews()
    
        j = j+1
end

In [31]:
GR.show()

GR.HTML("<video autoplay controls><source type=\"video/mp4\" src=\"data:video/mp4;base64,AAAAFGZ0eXBxdCAgAAACAHF0ICAAAAAId2lkZQA5BpptZGF0AAACsQYF//+t3EXpvebZSLeWLNgg2SPu73gyNjQgLSBjb3JlIDE2MyAtIEguMjY0L01QRUctNCBBVkMgY29kZWMgLSBDb3B5bGVmdCAyMDAzLTIwMjEgLSBodHRwOi8vd3d3LnZpZGVvbGFuLm9yZy94MjY0Lmh0bWwgLSBvcHRpb25zOiBjYWJhYz0xIHJlZj0zIGRlYmxvY2s9MTowOjAgYW5hbHlzZT0weDM6MHgxMTMgbWU9aGV4IHN1Ym1lPTcgcHN5PTEgcHN5X3JkPTEuMDA6MC4wMCBtaXhlZF9yZWY9MSBtZV9yYW5nZT0xNiBjaHJvbWFfbWU9MSB0cmVsbGlzPTEgOHg4ZGN0PTEgY3FtPTAgZGVhZHpvbmU9MjEsMTEgZmFzdF9wc2tpcD0xIGNocm9tYV9xcF9vZmZzZXQ9LTIgdGhyZWFkcz0xMiBsb29rYWhlYWRfdGhyZWFkcz0yIHNsaWNlZF90aHJlYWRzPTAgbnI9MCBkZWNpbWF0ZT0xIGludGVybGFjZWQ9MCBibHVyYXlfY29tcGF0PTAgY29uc3RyYWluZWRfaW50cmE9MCBiZnJhbWVzPTMgYl9weXJhbWlkPTIgYl9hZGFwdD0xIGJfYmlhcz0wIGRpcmVjdD0xIHdlaWdodGI9MSBvcGVuX2dvcD0wIHdlaWdodHA9MiBrZXlpbnQ9MjUwIGtleWludF9taW49MjQgc2NlbmVjdXQ9NDAgaW50cmFfcmVmcmVzaD0wIHJjX2xvb2thaGVhZD00MCByYz1hYnIgbWJ0cmVlPTEgYml0cmF0ZT00MDAwIHJhdGV0b2w9MS4wIHFjb21wPTAuNjAgcXBtaW49MCBxcG1heD02OSBxcHN0ZXA9NCBpcF9yYXRpbz0xLjQwIGFxPTE6MS4wMACAAADVG2WIhAAa//731LfMsu1Tb7YLqPeiniZfQ3UlAZuWxO06gAAAAwAAAwAAAwDpVIJjfO4A0Yy0AAAW43cqxW9GcwA/xIpoH0oiK0e6lVH4r43cNeuPzJijpQ8PVmBUHc/27v0J6vi2PmzIdBU6JN1XJZWIwH5bQyPdbzj01ocpcVhkHLxEJ6XUBK3ZBWNnsjjFzCXSpZg+aRVirLdKQim/Y9sjZw+RwU0ASkrwcOWTYw2/+e7XcVXrmhN5d0UbCxt8bejthpfjM0i8hv0q69aWnjEqyCmw++dH0+jdHkBbYCXZtqLgoZtywOYErIqkQTxTmoEkHItDxHDrTtlx+AsvM2p3faNFgngQnqqs5H+BWVIJvxaifcKiTmKEQ6xPWVTNhD6DgN9PnO/uYmnXq0zXYb3qctCsAvAsCu92xXBgCVk/R2cxJzkhvMg3QEYy6pI1/DRa/ZtsivvOMLN2PbwIjPmiux0O3uyGL/+R9m08x2omBwZ6NlVd2JIIyc2+i3V8DGPEmodA6Nb7BqKqa6WtsKvH10h0FXBpMHfROCptscMl0CvTYyWqtFlri+JE7tRz5HYcOqet/NK1hOeSjQgngbabd13hesxkuqvEN1zP8eR2o1Y+3lDzej7vpzv6dJgx5NBs/Sr+Xaf4w4uHKOdj3Mi063X2vAgeyktkC+iD0+p+1vL1RSvfVVFyPxVtAfDZ7EykKtPShQkQHuWhRrEnwiwUY+mzy70ZuV03VMppmCLlutR1Ynyg49dnUz2flvVyAcQzm+ztMFiz80L+b3evy8d1v5pRHhXkRU6XgV6+jKl9YJ1YKNE1VjqHg2ICX/sfmixkdC1N/45RBujNu8jm648MHt17M2yjKlLf4nHspYT2e4uXG/vrSZ9sdqkISAtyrWXTahlNpZ8XtTn6SE8hjsD6ZVyMeVbUYfvyRTr1WlNjcdPQnr5gHxCJ3/efYFoDJhAnI93iTzY5vPeO6PvuwOOWiTPFB5I661soY6dqgeu8jsC7FuLdNLi10+54+Wd0eLolMqBo61OJr0Xm+fwenUNrB09XTil/yz4m7i0wZHHWMW+XTjtnTWXgAFJBJqqv7zP9NF4bQKW/mz+A9ZEyWoclu/tY16fF6eLyTI1sVIwifP3Uif9SqQFwV0JcjvHytdASrWTtmbxx5geeja+u517v3UDbAzBH3pV2jezS5/z/tJ+G3IMJDECVQ2siQBLSQI4Rc6l/jCbE+M62tM5cBzMIzpPQx1q2CVF03zTfXOb4FR5G9So3qYBlMX42pvCcp5tPinPizitI9eQ/FbGkbvTIMovqpyh7QpieCCyQJWD9yZnamu3sEcsCaSfXab7QUFIigWFL5CuU9WS7plzxTY06qr4kJ3OJAajze3RNnQdzComA/z1e//UtIJA4bs/5yTjMin3EIb5nzAjuauZwELIOZjuARVKNyoWrVOFe5aPI7nyd0vyIg15nM2ALtUldggG5Z9vFHkv/IULE8zzNj+HJ3muf86hb/dGJSWYgadxX6LpvkId5EE9x0oPVxCbWYV1LS2RUGTqUw6wGbohYnCV/kvcVj9ItjtgAp6BfDYYGiatL6vipCgRk+ISggKSlX17BuofAEiNhtZAyxUQNYbrnl5ZTd/zOsX2bO0Wyz5op+uxakg++0CAenFBn9mXSY7PeWzHO/dKOWwBhkGBQ+nNJJ8QH1nIdhS5sWhohFCalr6qMvuVxMYttUQcB5DIRdirLk8Xlhiael2jgjq4gyT3JlQGOKdtiKVkCTaVpPMBLYINnQZryp+BP79gIOfCd+c3DxnUant4BkWqYXwl/CqvKmJEgJ/VxYQPc3zv8RS9F07ksBdxbKtCW7S33L69kRPYYDfWA1i/vldU3KepiOBZkp0UiDepLbSp7Zq13q/onFpeZvSKvaUgo2B+lJGz2qh9a9F7Fc2Vc2cz7Bbj0ncPctb1NckNUINRwKrUpveIgjwdrErOztNlI8hvp/58M3XtOQaWLQxs/EL6F8N1ZwyfxSOHaR7qifkiSC8b1k7enGdThyb1hXYgzXm2ILpBHOC8Op2RgP11TQpMhJjGiifeL9kCmjyqTSxSUY6V/gJRTswKq+4uF1B2IYRQUUvVIWQmzrd8uVnw5XYzV2iK4pSE+GIonrp8IkI6XcQwyPTTZWOTmCdnB2VASgbEFK8C10xgc1l2REfXQJ6DItaOtHZGVNnF/RYCIyjBPsMhV6aKgZugBvM39lTGUehNMbnxQD41G9aLBxHjN6kazU/1a48NYKK/5vfpodpRznSeLUT2CpCQbU1vxdG4vK/L4zGFH0gjTZNZZsFBd9y5zLwa83D7JdOZA34fo0n/9sVicfw6160Der544tZ/6QbW3lvHjCJfgKYjJXzytidECsjyQAjIRsFsfyIK2GDnGpl6DHZqDhoNJFRNdcadgaIdym25VoiYrMu9PvXePMJj3HmiaChLif3cVRj+6gTvSf/B/CjApkriKHQhPtwHBdg3BLxjQMDojhAwHADIu/Qninu458ZfnKNsdqQowjvhkz8XzrhD1XwrHgUUuLwjqkjgWqb6ZjnsbSzlRJUu44s1cbhVKs/QpwBhjhjV+l4ggFhlywsdJoi+Bi6ANZsTf2ytCF/8wKFHxPEjA0CY/GU2IEcOykhdCnWeZ78Xk2iuO4NAiJrZL/mPDav80CeoZ2tEhCyKv3EqKm35L4as0mjzqKfA+wxSnWBKgM+dpaHD6GWGgIgP7jGP7tT269g62yXVt5W5tQa6psKbtlZsBDO5cqipHKktGpIYnJEYrmt6Oji3o6nacS5dOL6hEMOXdaHbQiE0xck5l4KYRgvMm/rYEs+6y8pCiJb+jh2x9jyIVnwx1dh3+vTtptFJRRs8J/7iZefrpwDzvOcKhIvSeeWOdVXH945u3//7KhWaRtXrXt/1657rTs0gNdE1vH1L

In [26]:
menge.agent[1].vel

1.4989495345620312

In [56]:
Path = "/home/jakob/Dokumente/Sim_Data/"
dir = "UNI2_CollisionFree"
header = Header(p, p_desc, sim_p, sim_p_desc, op_model, tact_model, order, update, N, system_size);
Save_Data!(Path, dir, header, positions)

Created Directory /UNI2_CollisionFree.


In [23]:
Ns = 10:10:200

#### parameters of the agents ####
δt = 0.01
p = [1.4, 1.4, 3.0, 1.0, 0.3, 0.0, 0.0, 0.1, 5.0, 0.0, 0.0, 0.1, 0.6283185307179586]
p_desc = "v_max, v_des, T, T2, l, step_time, τ_A, τ_R, α, ζ_h, ζ_v, r, ϕ"

### of the system ###
system_size = (9.0, 5.0) #important for periodic boundaries

### of the simulation ###
sim_p = [30.0, 150.0, 0.05, δt, 3.0] #t_relax, t_max, dt_save, dt, r
sim_p_desc = "t_relax, t_max, dt_save, dt, r"

Random.seed!(786)

### initialize geometry ###
geometrie = create_geometry_single_obstacle((37.5,31.5), 0.0)


Path = "/home/jakob/Dokumente/Sim_Data/"
dir = "Uni_Dir_CollisionFree3"
N = 10
header = Header(p, p_desc, sim_p, sim_p_desc, op_model, tact_model, order, update, N, system_size);

In [24]:
for N in Ns#[1:2]
    
    Random.seed!()
    
    if mod(N, 10) == 0
        println(N)
    end

    ### initialize crowd ###
    menge = create_crowd(N, geometrie)
    Init_Hom_Parameters!(p, menge)
    Two_Approaching_Crowds(menge, geometrie, system_size[1], Int(round(N)), system_size)
    
    positions, headings, ttcs = Simulate!(menge, geometrie, sim_p[1], sim_p[2], sim_p[3], sim_p[4], sim_p[5], system_size);
    
    header = Header(p, p_desc, sim_p, sim_p_desc, op_model, tact_model, order, update, N, system_size)
    Save_Data!(Path, dir, header, positions)
    
end

10
20
30
40
50
60
70
80
90
100
110
120
130
140
150
160
170
180
190
200


In [ ]:
name = "Juelich_UNI_"
path = "/home/jakob/Dokumente/Renne_Software/UMANS_3/examples/agents/"


Set_Goal_from_E_des!(menge, (99.0, 0.0))
Change_Coordinate_System_Agents!(menge, -1 .*(system_size./2))
Write_Agents_XML(menge, name, path)

In [ ]:
path = "/home/jakob/Dokumente/Renne_Software/UMANS/examples/"
policy = "SocialForces"
agents = "Juelich_UNI_"

name = string(agents, policy)


Write_Scenario_XML(path, name, sim_p, system_size, policy, agents)